# Safer Parks: Capturing perceptions of safety using open data

In [1]:
import pandas as pd
import geopandas as gpd
import fiona
import osmnx as ox
from shapely.ops import unary_union
import re
import folium


In [2]:
# read in safer_parks_functions - see notebook for more details on functions
%run safer_parks_functions.ipynb

### Local Authoirty Approach

This analysis is designed to be run on a local authority by local authority basis as data availability tends to vary by local authority. We use [May 2024 Local Authority District (LAD) data](https://www.google.com/url?sa=t&source=web&rct=j&opi=89978449&url=https://geoportal.statistics.gov.uk/datasets/ons::local-authority-districts-may-2024-boundaries-uk-bfe-2/about&ved=2ahUKEwi83bT-pJGOAxWBUUEAHSA-NZsQFnoECAoQAQ&usg=AOvVaw3nYML7UR9GdX1gnUYTH8uz), however this can be updated as and when boundaries change. It is also possible to edit the code to change the geographies used by choosing a different shapefile boundary - e.g. focus on an entire unitary authority or metropolitan area, or focus on a specific town or village. 



## Defining park boundaries

Formal park boundary data may exist and be openly avialable for some planing or administrative areas, but often this data is not publicly available or formally defined. We define a process for defining public green space using two different data sources: OS Open Greenspace and Openstreet map. Both sources have their advantages and disadvatages, as outlined in the sections below.

We recommend comparing OS and Openstreetmap data in the UK. Outside the UK we recommend using Openstreet map unless a comparative alternative is available in your region. 



### OS Open Greenspace

In Great Britain the Ordanace Survey provide 'OS Open Greenspace'-  'Covering a range of greenspaces in urban and rural areas including playing fields, sports’ facilities, play areas and allotments.' The data is provided as polygons of the greenspace areas themseleves and entry points to the greensapce site as point data. 

## Openstreetmap Greenspace data


## Comparing Greenspace data 


### Parks in Bradford
In Bradford https://bradforddistrictparks.org/ provides data on formally recognised parks and greenspaces in Bradford. We web-scraped the parks website to get further information on parks faciltiies and define 'formal' aprks and greenspaces within Bradford.




https://osdatahub.os.uk/downloads/open/OpenGreenspace

In [3]:
# read in OS Open Greenspace data

print(fiona.listlayers('Data/opgrsp_gb.gpkg'))
os_greenspace_access =gpd.read_file('Data/opgrsp_gb.gpkg', layer ='access_point')
os_greenspace_site =gpd.read_file('Data/opgrsp_gb.gpkg', layer ='greenspace_site')

['access_point', 'greenspace_site']


In [4]:
# read in local authority shapefile 
LAD_2024 =gpd.read_file('Data/LAD_May_2024.geojson')

In [5]:
# get OS greenspaces sites in Bradford LAD
greenspace_sites_bradford = subset_to_LAD(LAD_gdf=LAD_2024, LAD_column_name='LAD24NM', LAD_name='Bradford', data_to_subset=os_greenspace_site)
# # combine greenspace sites that intersect or touch into one polygon
# greenspace_sites_bradford = merge_touching_or_intersecting_polygons(greenspace_sites_bradford)
# greenspace_sites_bradford = merge_touching_or_intersecting_polygons(greenspace_sites_bradford)
greenspace_sites_bradford

id               function  \
1       0A0C1723-E2A4-4FA1-B127-F73A7954FB7B  Public Park Or Garden   
151     2BE88DCC-827A-7FED-E063-AAEFA00A0EDD  Public Park Or Garden   
163     2BE88DCC-83BB-7FED-E063-AAEFA00A0EDD             Play Space   
605     2BE88DCC-D52D-7FED-E063-AAEFA00A0EDD  Other Sports Facility   
754     2BE88DCC-F082-7FED-E063-AAEFA00A0EDD             Play Space   
...                                      ...                    ...   
161497  2BE88F5F-A26E-7FED-E063-AAEFA00A0EDD          Playing Field   
161534  2BE88F5F-AA93-7FED-E063-AAEFA00A0EDD  Other Sports Facility   
161759  2BE88F5F-D91C-7FED-E063-AAEFA00A0EDD  Public Park Or Garden   
161827  2BE88F5F-E527-7FED-E063-AAEFA00A0EDD  Public Park Or Garden   
161953  EE031128-5137-4B16-A2A9-EF1B593B8A04  Other Sports Facility   

             distinctive_name_1 distinctive_name_2 distinctive_name_3  \
1       Shay Grange Crematorium                NaN                NaN   
151                         NaN                NaN                NaN   
163                         NaN                NaN                NaN   
605                         NaN                NaN                NaN   
754                 Attock Park                NaN                NaN   
...                         ...                ...                ...   
161497                      NaN                NaN                NaN   
161534                      NaN                NaN                NaN   
161759                      NaN                NaN                NaN   
161827                      NaN                NaN                NaN   
161953         Cottingley Manor                NaN                NaN   

       distinctive_name_4                                           geometry  
1                     NaN  MULTIPOLYGON (((413213.450 436356.550, 412835....  
151                   NaN  MULTIPOLYGON (((411387.950 437193.900, 411383....  
163                   NaN  MULTIPOLYGON (((403185.260 444445.820, 403177....  
605                   NaN  MULTIPOLYGON (((417825.010 434672.350, 417828....  
754                   NaN  MULTIPOLYGON (((418208.790 433169.630, 418211....  
...                   ...                                                ...  
161497                NaN  MULTIPOLYGON (((411672.850 437052.390, 411676....  
161534                NaN  MULTIPOLYGON (((413680.210 431865.180, 413682....  
161759                NaN  MULTIPOLYGON (((418047.600 430223.370, 418052....  
161827                NaN  MULTIPOLYGON (((414592.290 428702.530, 414583....  
161953                NaN  MULTIPOLYGON (((411925.750 437140.380, 411953....  

[1022 rows x 7 columns]

In [6]:
# get OS greenspaces access points in Bradford LAD
greenspace_access_bradford = subset_to_LAD(LAD_gdf=LAD_2024, LAD_column_name='LAD24NM', LAD_name='Bradford', data_to_subset=os_greenspace_access)
greenspace_access_bradford.explore()

In [7]:
##### Uncomment code to define GS using OSM instead od the OS Open Greenspace data, 
###### replace place name or polygon with area of interest 


# get OSM greenspaces
## Either using a placename or an shapefile to define the spatial limits of the data

# Define the tags for i.e. parks, woodlands, and scrublands
tags = {
    'leisure': ['park'],
    'landuse': ['forest', 'meadow'],
    'natural': ['wood', 'scrub']
}
################################################################################
#### Get the geometries for the specified place name and tags ####

# # Define the place name
# place_name = "Bradford, West Yorkshire, England"
# # get OSM geometries from palcename
# gdf = ox.geometries_from_place(place_name, tags)

############################ OR ################################################
#### Get the geometries for the specified polygon and tags ####

# define LAD of interest e.g. Bradford
bradford = LAD_2024.loc[LAD_2024['LAD24NM']=='Bradford',:]
# get OSM geometries from polygon boundary 
gdf = ox.geometries_from_polygon(bradford.to_crs("EPSG:4326").unary_union, tags)

################################################################################
# # Filter the geometries to include only parks, woodlands, and scrublands
osm_greenspace= gdf[gdf['leisure'].isin(['park'])|
                             gdf['landuse'].isin(['forest', 'meadow']) | 
                             gdf['natural'].isin(['wood', 'scrub'])].reset_index()

#osm_greenspace = merge_touching_or_intersecting_polygons(osm_greenspace)
osm_greenspace 

/var/folders/78/m__nl8h97l7358p69kgvvz_c0000gp/T/ipykernel_67072/499009049.py:28: FutureWarning: The `geometries` module and `geometries_from_X` functions have been renamed the `features` module and `features_from_X` functions. Use these instead. The `geometries` module and function names are deprecated and will be removed in the v2.0.0 release. See the OSMnx v2 migration guide: https://github.com/gboeing/osmnx/issues/1123
  gdf = ox.geometries_from_polygon(bradford.to_crs("EPSG:4326").unary_union, tags)


element_type     osmid access barrier  \
0             way   4472848    NaN     NaN   
1             way   4483806    NaN     NaN   
2             way   4535372    NaN     NaN   
3             way   4535557    NaN     NaN   
4             way   4536859    NaN     NaN   
...           ...       ...    ...     ...   
3145     relation  16458862    NaN     NaN   
3146     relation  16493384    NaN     NaN   
3147     relation  16618634    NaN     NaN   
3148     relation  17373549    NaN     NaN   
3149     relation  18547922    NaN     NaN   

                                               geometry              source  \
0     POLYGON ((-1.74235 53.91227, -1.74210 53.91220...                 NaN   
1     POLYGON ((-1.74985 53.91496, -1.74974 53.91512...                 NaN   
2     POLYGON ((-1.81990 53.92424, -1.81964 53.92424...                 NaN   
3     POLYGON ((-1.82648 53.92484, -1.82659 53.92463...                 NaN   
4     POLYGON ((-1.82357 53.92632, -1.82360 53.92627...  interpolation;Bing   
...                                                 ...                 ...   
3145  POLYGON ((-1.78064 53.92493, -1.78056 53.92494...                 NaN   
3146  POLYGON ((-1.75957 53.92112, -1.75960 53.92115...                Bing   
3147  POLYGON ((-1.75531 53.89982, -1.75465 53.90013...                 NaN   
3148  POLYGON ((-1.76340 53.86633, -1.76274 53.86657...                 NaN   
3149  POLYGON ((-1.74338 53.75393, -1.74356 53.75349...                 NaN   

                      name addr:city addr:housenumber addr:postcode  ...  \
0     Burley Village Green       NaN              NaN           NaN  ...   
1            Victoria Park       NaN              NaN           NaN  ...   
2                      NaN       NaN              NaN           NaN  ...   
3              Canker Well       NaN              NaN           NaN  ...   
4                      NaN       NaN              NaN           NaN  ...   
...                    ...       ...              ...           ...  ...   
3145                   NaN       NaN              NaN           NaN  ...   
3146           Jerry Holme       NaN              NaN           NaN  ...   
3147                   NaN       NaN              NaN           NaN  ...   
3148     Hawksworth Spring       NaN              NaN           NaN  ...   
3149                   NaN       NaN              NaN           NaN  ...   

     source:alt_name landcover addr:housename addr:village source:geometry  \
0                NaN       NaN            NaN          NaN             NaN   
1                NaN       NaN            NaN          NaN             NaN   
2                NaN       NaN            NaN          NaN             NaN   
3                NaN       NaN            NaN          NaN             NaN   
4                NaN       NaN            NaN          NaN             NaN   
...              ...       ...            ...          ...             ...   
3145             NaN       NaN            NaN          NaN             NaN   
3146             NaN       NaN            NaN          NaN             NaN   
3147             NaN       NaN            NaN          NaN             NaN   
3148             NaN       NaN            NaN          NaN             NaN   
3149             NaN       NaN            NaN          NaN             NaN   

     historic:ref:1835_tithe_award sport fixme                      ways  \
0                              NaN   NaN   NaN                       NaN   
1                              NaN   NaN   NaN                       NaN   
2                              NaN   NaN   NaN                       NaN   
3                              NaN   NaN   NaN                       NaN   
4                              NaN   NaN   NaN                       NaN   
...                            ...   ...   ...                       ...   
3145                           NaN   NaN   NaN    [91889679, 1214074937]   
3146                           NaN   NaN   Na

In [8]:
# Get OS greenspace cols to join
os_gs_to_join =greenspace_sites_bradford[['distinctive_name_1','function','id','geometry']]
os_gs_to_join.columns = ['Name (OS)', 'Type (OS)', 'OS ID', 'geometry' ]


# Get OSM greenspace cols to join
# combine OSM tags into one value
osm_greenspace['Type (OSM)'] =osm_greenspace[['natural', 'leisure', 'landuse']].apply(lambda x: ', '.join(sorted(x.dropna().astype(str))),axis=1)

osm_gs_to_join = osm_greenspace[['name','Type (OSM)','osmid','geometry']]
osm_gs_to_join.columns = ['Name (OSM)', 'Type (OSM)', 'OSM ID', 'geometry' ]

# change crs before joining
osm_gs_to_join= osm_gs_to_join.to_crs(os_gs_to_join.crs)
# append OSM data to OS data
os_osm_greenspace_bradford =pd.concat([os_gs_to_join,osm_gs_to_join])

# unify greenspace geographies, keepign type data
os_osm_greenspace_bradford =merge_touching_or_intersecting_polygons_condense(os_osm_greenspace_bradford)

# remove duplicate information in variables, generated during process of combining into one geometry
os_osm_greenspace_bradford['Name (OS)'] =os_osm_greenspace_bradford['Name (OS)'].apply(lambda x: ', '.join(sorted(set(map(str.strip, str(x).split(','))))) if pd.notnull(x) else x).apply(lambda x: re.sub(r'(?<!\w),', '', x))
os_osm_greenspace_bradford['Name (OSM)'] =os_osm_greenspace_bradford['Name (OSM)'].apply(lambda x: ', '.join(sorted(set(map(str.strip, str(x).split(','))))) if pd.notnull(x) else x).apply(lambda x: re.sub(r'(?<!\w),', '', x))

os_osm_greenspace_bradford['Type (OS)'] =os_osm_greenspace_bradford['Type (OS)'].apply(lambda x: ', '.join(sorted(set(map(str.strip, str(x).split(', '))))) if pd.notnull(x) else x).apply(lambda x: re.sub(r'(?<!\w),', '', x))
os_osm_greenspace_bradford['Type (OSM)'] =os_osm_greenspace_bradford['Type (OSM)'].apply(lambda x: ', '.join(sorted(set(map(str.strip, str(x).split(', '))))) if pd.notnull(x) else x).apply(lambda x: re.sub(r'(?<!\w),', '', x))

os_osm_greenspace_bradford['OS ID'] = os_osm_greenspace_bradford['OS ID'].apply(lambda x: ', '.join(sorted(set(map(str.strip, str(x).split(', '))))) if pd.notnull(x) else x).apply(lambda x: re.sub(r'(?<!\w),', '', x))
os_osm_greenspace_bradford['OSM ID'] = os_osm_greenspace_bradford['OSM ID'].apply(lambda x: ', '.join(sorted(set(map(str.strip, str(x).split(', '))))) if pd.notnull(x) else x).apply(lambda x: re.sub(r'(?<!\w),', '', x))

In [9]:
os_osm_greenspace_bradford.explore()

/Users/fran/anaconda3/envs/geog_env/lib/python3.11/site-packages/folium/features.py:1155: UserWarning: GeoJsonTooltip is not configured to render for GeoJson GeometryCollection geometries. Please consider reworking these features: [{'Name (OS)': '', 'Type (OS)': ' ', 'OS ID': ' ', 'Name (OSM)': ' Cringles Plantation, Little Sea Moor', 'Type (OSM)': 'meadow, wood', 'OSM ID': '1334814971.0, 1354777437.0, 1355127608.0, 1355127613.0, 1355127624.0, 1355127626.0, 1355127630.0, 1355127648.0, 1355127654.0, 1355127658.0, 1355127660.0, 1359967022.0, 1359968748.0, 1359968752.0, 1359968754.0, 1359979811.0, 1360767488.0, 1360767493.0, 1360767497.0, 1360767499.0, 1360767505.0, 1360767508.0, 1360767512.0, 1360767523.0, 1360767528.0, 1360769053.0, 1360769055.0, 1360769056.0, 1360769057.0, 1360769060.0, 1360769061.0, 1360769064.0, 1360769065.0, 1360769066.0, 1360769067.0, 1360769069.0, 1361072023.0, 1361072024.0, 1361072026.0, 1361072028.0, 1361072032.0, 1361072036.0, 1361072038.0, 1361072048.0, 136107

In [10]:
# Defining parks

# Data scraped from: 'https://bradforddistrictparks.org/park/page/'
bd_parks= gpd.read_file('Data/bradford_district_parks.geojson')
bd_parks.explore()

In [11]:
# os_osm_greenspace_bradford_buffer = os_osm_greenspace_bradford
# os_osm_greenspace_bradford_buffer['geometry'] =os_osm_greenspace_bradford_buffer.buffer(50)


# test =gpd.sjoin(os_osm_greenspace_bradford_buffer, bd_parks.to_crs(os_osm_greenspace_bradford_buffer.crs), predicate='intersects', how='left')

# test.loc[test['Park Name'].isna()==True, 'BMDC_park']= 'No'
# test.loc[test['Park Name'].isna()==False, 'BMDC_park']= 'BMDC Park'

In [111]:
##### combine bradford parks data from website with OSM and OS combined greensapce data
# cerate a copy
bd_parks_polygon= bd_parks
# remove geom column (for now)
bd_parks_polygon =bd_parks_polygon.drop(columns=['geometry'])
bd_parks_polygon = bd_parks_polygon.reset_index()

# idenitfy where bradford park anmes exactly match the OS or OSM Name
bd_parks_polygon_1 =bd_parks_polygon.merge(os_osm_greenspace_bradford, right_on='Name (OS)',left_on='Park Name', how='left')
bd_parks_polygon_2 =bd_parks_polygon.merge(os_osm_greenspace_bradford, right_on='Name (OSM)',left_on='Park Name', how='left')

# remove null rows after join
bd_parks_polygon_1 =bd_parks_polygon_1.dropna(subset=['OS ID','OSM ID'])
bd_parks_polygon_2 =bd_parks_polygon_2.dropna(subset=['OS ID','OSM ID'])

# combine the exact match data into one geodataframe
bd_parks_polygon_1_2 =gpd.GeoDataFrame(pd.concat([bd_parks_polygon_1,bd_parks_polygon_2]).drop_duplicates('index'))

# use the exact match data to identify the remiaingn bmdc parks without os or osm greenspace data
bd_parks_polygon_3 =bd_parks_polygon[~bd_parks_polygon['index'].isin(bd_parks_polygon_1_2['index'])]
# and save as bd_parks_polygon_3
bd_parks_polygon_3 =gpd.GeoDataFrame(bd_parks_polygon_3, geometry=gpd.points_from_xy(bd_parks_polygon_3.Longitude, bd_parks_polygon_3.Latitude, crs="EPSG:4326"))

# ## Uncomment if want to do sjoin on buffer in future
# os_osm_greenspace_bradford_buffer = os_osm_greenspace_bradford
# os_osm_greenspace_bradford_buffer['geometry'] =os_osm_greenspace_bradford.buffer(30)

# spaially join bmdc park points to os and OSM greenspace data
bd_parks_polygon_3 =gpd.sjoin(bd_parks_polygon_3.to_crs(os_osm_greenspace_bradford.crs),os_osm_greenspace_bradford, predicate='intersects', how='left')

###### come back to later- bmdc parks on website that do not have an easily identifiable open counterpart #####
#(either due to lack of spatial info on bmdc, innacurate locaiton or incosnsitent naming)
bd_parks_polygon_4 =bd_parks_polygon_3[bd_parks_polygon_3['index_right'].isna()]


bd_parks_polygon_3=bd_parks_polygon_3[~bd_parks_polygon_3['index_right'].isna()]
# define bradford parks as those with an exact name or spatial join match (43/71 parks, a remaining 10 aprks do have long/lat info)
bradford_parks_gdf =gpd.GeoDataFrame(pd.concat([bd_parks_polygon_1,bd_parks_polygon_2,bd_parks_polygon_3]).drop_duplicates('index'))




In [15]:
bradford_parks_gdf

index                         Park Name  \
5       5                 Russell Hall Park   
6       6                    Greenwood Park   
7       7                       Grange Park   
8       8                      Foxhill Park   
14     14                      Knowles Park   
23     23  Seymour Street Recreation Ground   
26     26                   Eccleshill Park   
28     28                  Cross Roads Park   
40     40                       Wibsey Park   
49     49              Prince of Wales Park   
50     50                         Peel Park   
53     53                         Lund Park   
54     54                   Littlemoor Park   
55     55                     Ladyhill Park   
56     56                       Horton Park   
59     59                       Foster Park   
60     60                   Devonshire Park   
61     61                     Crowgill Park   
62     62                  Cross Roads Park   
65     65                  Brackenhill Park   
66     66                       Lister Park   
69     69                Bradford Moor Park   
16     16                     Parkside Park   
34     34                        Judy Woods   
35     35                        Griff Wood   
46     46                      Silsden Park   
47     47              Shipley Central Park   
9       9         Riverside Gardens, Ilkley   
37     37                    Crabtree Ghyll   
38     38                         Buck Wood   
41     41             West Park, Girlington   
42     42          Victoria Park, Oakenshaw   
43     43           Victoria Park, Keighley   
44     44            Victoria Park, Clayton   
48     48                      Roberts Park   
51     51                       Myrtle Park   
52     52                      Menston Park   
57     57       Holden Park (Oakworth Park)   
58     58                       Harold Park   
63     63       Cliffe Castle Museum & Park   
64     64             Central Park, Haworth   
67     67                   Middleton Woods   
68     68                  Northcliffe Park   

                                             Park URL  \
5   https://bradforddistrictparks.org/park/russell...   
6   https://bradforddistrictparks.org/park/greenwo...   
7   https://bradforddistrictparks.org/park/grange-...   
8   https://bradforddistrictparks.org/park/foxhill...   
14  https://bradforddistrictparks.org/park/knowles...   
23  https://bradforddistrictparks.org/park/seymour...   
26  https://bradforddistrictparks.org/park/ecclesh...   
28  https://bradforddistrictparks.org/park/cross-r...   
40  https://bradforddistrictparks.org/park/wibsey-...   
49  https://bradforddistrictparks.org/park/prince-...   
50  https://bradforddistrictparks.org/park/peel-park/   
53  https://bradforddistrictparks.org/park/lund-park/   
54  https://bradforddistrictparks.org/park/littlem...   
55  https://bradforddistrictparks.org/park/ladyhil...   
56  https://bradforddistrictparks.org/park/horton-...   
59  https://bradforddistrictparks.org/park/foster-...   
60  https://bradforddistrictparks.org/park/devonsh...   
61  https://bradforddistrictparks.org/park/crowgil...   
62  https://bradforddistrictparks.org/park/cross-r...   
65  https://bradforddistrictparks.org/park/bracken...   
66  https://bradforddistrictparks.org/park/lister-...   
69  https://bradforddistrictparks.org/park/bradfor...   
16  https://bradforddistrictparks.org/park/parksid...   
34  https://bradforddistrictparks.org/park/judy-wo...   
35  https://bradforddistrictparks.org/park/griff-w...   
46  https://bradforddistrictparks.org/park/silsden...   
47  https://bradforddistrictparks.org/park/shipley...   
9   https://bradforddistrictparks.org/park/riversi...   
37  https://bradforddistrictparks.org/park/crabtre...   
38  https://bradforddistrictparks.org/park/buck-wood/   
41  https://bradforddistrictparks.org/park/west-pa...   
42  https://bradforddistrictparks.org/park/victori...   
43  https://bradforddistrictparks.org/park/victori... 

In [109]:
#### NEED TO BUG SOLVE ONLY SAVING POLYGON_3 as points. 
bd_parks_polygon_3.explore()

In [69]:

# get boundsing box of 400m arround each park to calcualte network connectivity 
bradford_parks_gdf =bradford_parks_gdf.to_crs('EPSG:2770')
# conver back to 4326 after buffer for bbox crs
cols =bradford_parks_gdf.buffer(400).to_crs('EPSG:4326').bounds.add_prefix('400m_bounding_').columns
bradford_parks_gdf[cols]= bradford_parks_gdf.buffer(400).to_crs('EPSG:4326').bounds.add_prefix('400m_bounding_')
bradford_parks_gdf

index                         Park Name  \
5       5                 Russell Hall Park   
6       6                    Greenwood Park   
7       7                       Grange Park   
8       8                      Foxhill Park   
14     14                      Knowles Park   
23     23  Seymour Street Recreation Ground   
26     26                   Eccleshill Park   
28     28                  Cross Roads Park   
40     40                       Wibsey Park   
49     49              Prince of Wales Park   
50     50                         Peel Park   
53     53                         Lund Park   
54     54                   Littlemoor Park   
55     55                     Ladyhill Park   
56     56                       Horton Park   
59     59                       Foster Park   
60     60                   Devonshire Park   
61     61                     Crowgill Park   
62     62                  Cross Roads Park   
65     65                  Brackenhill Park   
66     66                       Lister Park   
69     69                Bradford Moor Park   
16     16                     Parkside Park   
34     34                        Judy Woods   
35     35                        Griff Wood   
46     46                      Silsden Park   
47     47              Shipley Central Park   
9       9         Riverside Gardens, Ilkley   
37     37                    Crabtree Ghyll   
38     38                         Buck Wood   
41     41             West Park, Girlington   
42     42          Victoria Park, Oakenshaw   
43     43           Victoria Park, Keighley   
44     44            Victoria Park, Clayton   
48     48                      Roberts Park   
51     51                       Myrtle Park   
52     52                      Menston Park   
57     57       Holden Park (Oakworth Park)   
58     58                       Harold Park   
63     63       Cliffe Castle Museum & Park   
64     64             Central Park, Haworth   
67     67                   Middleton Woods   
68     68                  Northcliffe Park   

                                             Park URL  \
5   https://bradforddistrictparks.org/park/russell...   
6   https://bradforddistrictparks.org/park/greenwo...   
7   https://bradforddistrictparks.org/park/grange-...   
8   https://bradforddistrictparks.org/park/foxhill...   
14  https://bradforddistrictparks.org/park/knowles...   
23  https://bradforddistrictparks.org/park/seymour...   
26  https://bradforddistrictparks.org/park/ecclesh...   
28  https://bradforddistrictparks.org/park/cross-r...   
40  https://bradforddistrictparks.org/park/wibsey-...   
49  https://bradforddistrictparks.org/park/prince-...   
50  https://bradforddistrictparks.org/park/peel-park/   
53  https://bradforddistrictparks.org/park/lund-park/   
54  https://bradforddistrictparks.org/park/littlem...   
55  https://bradforddistrictparks.org/park/ladyhil...   
56  https://bradforddistrictparks.org/park/horton-...   
59  https://bradforddistrictparks.org/park/foster-...   
60  https://bradforddistrictparks.org/park/devonsh...   
61  https://bradforddistrictparks.org/park/crowgil...   
62  https://bradforddistrictparks.org/park/cross-r...   
65  https://bradforddistrictparks.org/park/bracken...   
66  https://bradforddistrictparks.org/park/lister-...   
69  https://bradforddistrictparks.org/park/bradfor...   
16  https://bradforddistrictparks.org/park/parksid...   
34  https://bradforddistrictparks.org/park/judy-wo...   
35  https://bradforddistrictparks.org/park/griff-w...   
46  https://bradforddistrictparks.org/park/silsden...   
47  https://bradforddistrictparks.org/park/shipley...   
9   https://bradforddistrictparks.org/park/riversi...   
37  https://bradforddistrictparks.org/park/crabtre...   
38  https://bradforddistrictparks.org/park/buck-wood/   
41  https://bradforddistrictparks.org/park/west-pa...   
42  https://bradforddistrictparks.org/park/victori...   
43  https://bradforddistrictparks.org/park/victori... 

In [64]:
import osmnx as ox

In [77]:
# G = ox.graph_from_bbox(bradford_parks_gdf.iloc[0]['400m_bounding_maxy'],
#                         bradford_parks_gdf.iloc[0]['400m_bounding_miny'],
#                         bradford_parks_gdf.iloc[0]['400m_bounding_maxx'],
#                         bradford_parks_gdf.iloc[0]['400m_bounding_minx'],
#                         network_type='walk')

# # Calculate the number of corners (nodes with degree 3 or more)
# corners = [node for node, degree in dict(G.degree()).items() if degree >= 3]
# num_corners = len(corners)

# # Calculate the connectiveness (average node degree)
# avg_node_degree = sum(dict(G.degree()).values()) / len(G.nodes)

# print(f"Number of corners: {num_corners}")
# print(f"Connectiveness (average node degree): {avg_node_degree:.2f}")


# # Convert the network into a GeoDataFrame
# gdf_nodes, gdf_edges = ox.graph_to_gdfs(G)

# g

/var/folders/78/m__nl8h97l7358p69kgvvz_c0000gp/T/ipykernel_67072/3514160757.py:1: FutureWarning: The `north`, `south`, `east`, and `west` parameters are deprecated and will be removed in the v2.0.0 release. Use the `bbox` parameter instead. See the OSMnx v2 migration guide: https://github.com/gboeing/osmnx/issues/1123
  G = ox.graph_from_bbox(bradford_parks_gdf.iloc[0]['400m_bounding_maxy'],


Number of corners: 210
Connectiveness (average node degree): 4.71


In [95]:
# calculate n corners and connectedness of each network arround each park in the gdf 
bradford_parks_gdf['avg_node_degree_400m_network']=''
bradford_parks_gdf['n_corners_400m_nework']=''
for i in range(0,bradford_parks_gdf.shape[0]):  
    bbox=(
        bradford_parks_gdf.iloc[i]['400m_bounding_maxy'],
        bradford_parks_gdf.iloc[i]['400m_bounding_miny'],
        bradford_parks_gdf.iloc[i]['400m_bounding_maxx'],
        bradford_parks_gdf.iloc[i]['400m_bounding_minx']
        )  
    G = ox.graph_from_bbox(bbox=bbox,
                            network_type='walk')

    # Calculate the number of corners (nodes with degree 3 or more)
    corners = [node for node, degree in dict(G.degree()).items() if degree >= 3]
    num_corners = len(corners)

    # Calculate the connectiveness (average node degree)
    avg_node_degree = sum(dict(G.degree()).values()) / len(G.nodes)
    
    bradford_parks_gdf.loc[bradford_parks_gdf.index[i], 'avg_node_degree_400m_network'] = avg_node_degree.astype(float)
    bradford_parks_gdf.loc[bradford_parks_gdf.index[i], 'n_corners_400m_network'] = num_corners


    print(f"Number of corners: {num_corners}")
    print(f"Connectiveness (average node degree): {avg_node_degree:.2f}")


    # Convert the network into a GeoDataFrame
    #gdf_nodes, gdf_edges = ox.graph_to_gdfs(G)

Number of corners: 210
Connectiveness (average node degree): 4.71
Number of corners: 82
Connectiveness (average node degree): 4.68


Number of corners: 322
Connectiveness (average node degree): 5.10
Number of corners: 133
Connectiveness (average node degree): 4.64
Number of corners: 339
Connectiveness (average node degree): 4.88
Number of corners: 215
Connectiveness (average node degree): 5.13
Number of corners: 189
Connectiveness (average node degree): 5.08
Number of corners: 108
Connectiveness (average node degree): 4.70
Number of corners: 297
Connectiveness (average node degree): 4.91
Number of corners: 184
Connectiveness (average node degree): 4.60
Number of corners: 619
Connectiveness (average node degree): 5.32
Number of corners: 346
Connectiveness (average node degree): 5.29
Number of corners: 172
Connectiveness (average node degree): 4.87
Number of corners: 197
Connectiveness (average node degree): 4.79
Number of corners: 426
Connectiveness (average node degree): 5.08
Number of corners: 214
Connectiveness (average node degree): 4.91
Number of corners: 348
Connectiveness (average node degree): 5.21
Number of 